In [1]:
import xgboost as xgb
from sklearn.model_selection import train_test_split, StratifiedKFold, GridSearchCV, cross_validate
import matplotlib.pylab as pl
import pandas as pd
import numpy as np
import sklearn.metrics as metrics
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split
import xgboost
import shap
import numpy as np
import matplotlib.pylab as pl
import pandas as pd
from sklearn.preprocessing import LabelBinarizer

import pandas as pd
import pickle
from tqdm import tqdm


import statistics 
import math
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

# print the JS visualization code to the notebook
shap.initjs()

/aul/homes/msobh002/.conda/envs/concreteAE/lib/python3.9/site-packages/pandas/core/computation/expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.7.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/aul/homes/msobh002/.conda/envs/concreteAE/lib/python3.9/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.2' currently installed).
  from pandas.core import (
/aul/homes/msobh002/.conda/envs/concreteAE/lib/python3.9/site-packages/xgboost/core.py:265: FutureWarning: Your system has an old version of glibc (< 2.28). We will stop supporting Linux distros with glibc older than 2.28 after **May 31, 2025**. Please upgrade to a recent Linux distro (with glibc 2.28+) to use future versions of XGBoost.
Note: You have installed the 'manylinux2014' variant of XGBoost. Certain features such as GPU algorithms or federated learning are not av

# LUAD LUSC Healthy

In [2]:
map_dict = {
    "healthy":0,
    "luad": 1,
    "lusc":2   
}

In [3]:
map_dict = {
    "healthy":0,
    "luad": 1,
    "lusc":2   
}

# filtering samlples based on true predicted label
# now each sample will have the shap value of only one class (truly predicted class)

def filter_shap(test_data, shap_arr, y_map_new):
    df_data = []
#     ids_list = X_test.index.to_list()
#     genes_list = X_test.columns.tolist()
    ids_list = test_data.index.to_list()
    genes_list = test_data.columns.tolist()
    genes_list= genes_list[0:19648]
    
    for i in tqdm(range(shap_arr.shape[0])):
        sample = shap_arr[i]
        #print(sample)
        sample_id = ids_list[i]
        #print(sample_id)
        #print(y_pred[i])
        #label = inv_map[y_pred[i]]
        label = y_map_new['pred'][i]
        label= map_dict[label]
#         print(label)
#         _, w, h = sample.shape
        w, h = sample.shape
        #print(w,h)
        #print(sample[6])
        shap_scores_flat = sample[label][: len(genes_list)]
        #shap_scores_flat = np.reshape(sample[6], (w * h,))[: len(genes_list)]

        df_data.append([sample_id, *list(shap_scores_flat), label])

    shap_df = pd.DataFrame(
        data=np.array(df_data), columns=["id", *genes_list, "predicted_label"]
    )

    shap_df.set_index("id", inplace=True)
    shap_df["true_label"] = list(y_map_new['true_label'])
#     shap_df["predicted_label"] = shap_df["predicted_label"].astype("int").map(map_dict)
    #shap_df["predicted_label"] = shap_df["predicted_label"].map(map_dict)

    return shap_df



In [4]:
# drop falsely predicted samples by the model
def drop_false_pred(df):
    #df = df[df.predicted_label == df.true_label].copy()
    df = df[df.predicted_label.astype(int) == df.true_label.astype(int)].copy()
    df.drop("predicted_label", axis=1, inplace=True),
    return df

# get the ranking of genes for each class based on SHAP values
def get_rank_df(df):
    df = drop_false_pred(df)
    shap_df = df.loc[:, df.columns != "true_label"].astype("float64")
    #print(shap_df.shape)
    shap_df["true_label"] = df["true_label"]
    
    #taking the average that describes average cohort impact
    median_shap = shap_df.groupby("true_label").median() 
    median_shap = median_shap.T
    #print(median_shap)

    rank_dict = {}
    for col in median_shap:
        #print(col)
        sorted_df = median_shap.sort_values(by=col, ascending=False)
        #print(sorted_df)
        rank_dict[col] = sorted_df.index
    rank_df = pd.DataFrame.from_dict(rank_dict)
    #print(rank_df)
    return rank_df

In [5]:
output_dir= "../Output/luad_lusc_healthy/"
pd.read_csv(output_dir+"true_predicted_label_test_"+str('1')+"_xgboost.csv")

Sample    class     pred  true_label  pred_label
0    TCGA-55-7283-01A     luad     luad           1           1
1    TCGA-55-8208-01A     luad     luad           1           1
2    TCGA-44-8117-01A     luad     luad           1           1
3    TCGA-MP-A4TA-01A     luad     luad           1           1
4    TCGA-86-8669-01A     luad     luad           1           1
..                ...      ...      ...         ...         ...
182  GTEX-XYKS-0526-S  healthy  healthy           0           0
183  GTEX-YFC4-1126-S  healthy  healthy           0           0
184  GTEX-X5EB-0426-S  healthy  healthy           0           0
185  GTEX-ZXG5-0826-S  healthy  healthy           0           0
186  GTEX-XBEC-1026-S  healthy  healthy           0           0

[187 rows x 5 columns]

In [46]:
import matplotlib.pyplot as plt

model_dir= "../models/luad_lusc_healthy/"
output_dir= "../Output/luad_lusc_healthy/"
    
# loading truly predicted test file
newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str("1")+"_xgboost.csv")
newdftest.index= newdftest["Sample"]
newdftest=newdftest.drop(["Sample"], axis="columns")
X_test= newdftest.copy() 
print(X_test.shape)
print(X_test.index)

# loading truly predicted y_map
y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost.csv")
y_map_new.index= y_map_new["Sample"]
y_map_new=y_map_new.drop(["Sample"], axis='columns')
print(y_map_new.shape)

# loading saved model
mcl = xgb.XGBRFClassifier()
mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost.json")

# tree explainer; mcl is the model of xgboost
explainer = shap.TreeExplainer(mcl)

    
    
    

    
    

(187, 19648)
Index(['TCGA-55-7283-01A', 'TCGA-55-8208-01A', 'TCGA-44-8117-01A',
       'TCGA-MP-A4TA-01A', 'TCGA-86-8669-01A', 'TCGA-86-8668-01A',
       'TCGA-44-A4SS-01A', 'TCGA-55-7227-01A', 'TCGA-50-5936-01A',
       'TCGA-55-A48Z-01A',
       ...
       'GTEX-QV44-0926-S', 'GTEX-S4Z8-0426-S', 'GTEX-POYW-1226-S',
       'GTEX-U8T8-2226-S', 'GTEX-ZYFG-0226-S', 'GTEX-XYKS-0526-S',
       'GTEX-YFC4-1126-S', 'GTEX-X5EB-0426-S', 'GTEX-ZXG5-0826-S',
       'GTEX-XBEC-1026-S'],
      dtype='object', name='Sample', length=187)
(180, 4)


/aul/homes/msobh002/.conda/envs/concreteAE/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [03:20:05] WARNING: /workspace/src/learner.cc:872: Found JSON model saved before XGBoost 1.6, please save the model using current version again. The support for old JSON model will be discontinued in XGBoost 2.3.
  warnings.warn(smsg, UserWarning)


In [47]:
shap_values_list = []

explainer = shap.TreeExplainer(mcl)
shap_values = explainer(X_test)  # Get SHAP values for the patient
shap_values_list.append(shap_values)

shap_values_list

[.values =
 array([[[-1.57476647e-03,  9.67944413e-03, -1.10657774e-02],
         [-1.11444351e-04,  1.22858648e-04, -5.44170523e-03],
         [-3.06638103e-04, -7.33581837e-05, -2.73649325e-03],
         ...,
         [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
         [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
         [ 0.00000000e+00,  1.62071039e-04,  0.00000000e+00]],
 
        [[-1.68239279e-03,  2.83549819e-03, -1.76223076e-03],
         [ 4.15611248e-06, -2.67467392e-03,  3.69421585e-04],
         [-1.61214154e-02,  8.54744925e-04, -1.58214069e-03],
         ...,
         [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
         [ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
         [ 0.00000000e+00, -8.42326790e-06,  0.00000000e+00]],
 
        [[-4.19126387e-04,  9.32959467e-03, -2.46751471e-03],
         [ 4.15611248e-06,  6.02675369e-04,  6.92633737e-04],
         [ 2.17357156e-04, -7.04366976e-05, -2.49371561e-03],
         ...,
         [ 

In [50]:
explainer.expected_value

[0.4280438, 0.9823561, 0.5210734]

In [51]:
i=0
which_class= y_map_new['pred_label'][i]
display(shap.force_plot(explainer.expected_value[0], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[i],   X_test.values[i], feature_names = X_test.columns, link="logit"))

/tmp/ipykernel_29832/2511274794.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  which_class= y_map_new['pred_label'][i]


In [52]:
i=0
which_class= y_map_new['pred_label'][i]
display(shap.force_plot(explainer.expected_value[1], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[i],   X_test.values[i], feature_names = X_test.columns, link="logit"))

/tmp/ipykernel_29832/2381673129.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  which_class= y_map_new['pred_label'][i]


In [53]:
i=0
which_class= y_map_new['pred_label'][i]
display(shap.force_plot(explainer.expected_value[2], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[i],   X_test.values[i], feature_names = X_test.columns, link="logit"))

/tmp/ipykernel_29832/4274013107.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  which_class= y_map_new['pred_label'][i]


In [49]:
# Now, draw SHAP force plots for each class
for i, shap_values in enumerate(shap_values_list):
    plt.figure()
    shap.force_plot(explainer.expected_value, shap_values.values, X_test, link='logit')
    plt.title(f'SHAP Force Plot for Class {i+1}')
    plt.show()

TypeError: In v0.20, force plot now requires the base value as the first parameter! Try shap.plots.force(explainer.expected_value, shap_values) or for multi-output models try shap.plots.force(explainer.expected_value[0], shap_values[..., 0]).

<Figure size 432x288 with 0 Axes>

In [9]:
y_map_new

class     pred  true_label  pred_label
Sample                                                    
TCGA-55-7283-01A     luad     luad           1           1
TCGA-55-8208-01A     luad     luad           1           1
TCGA-44-8117-01A     luad     luad           1           1
TCGA-MP-A4TA-01A     luad     luad           1           1
TCGA-86-8669-01A     luad     luad           1           1
...                   ...      ...         ...         ...
GTEX-XYKS-0526-S  healthy  healthy           0           0
GTEX-YFC4-1126-S  healthy  healthy           0           0
GTEX-X5EB-0426-S  healthy  healthy           0           0
GTEX-ZXG5-0826-S  healthy  healthy           0           0
GTEX-XBEC-1026-S  healthy  healthy           0           0

[187 rows x 4 columns]

In [61]:
i=0
display(shap.force_plot(explainer.expected_value[0], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[0],   X_test.values[0], feature_names = X_test.columns, link="logit"))

In [62]:
i=0

display(shap.force_plot(explainer.expected_value[1], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[1],   X_test.values[0], feature_names = X_test.columns, link="logit"))

In [63]:
i=0
display(shap.force_plot(explainer.expected_value[2], shap.TreeExplainer(mcl).shap_values(X_test)[0].T[2],   X_test.values[0], feature_names = X_test.columns, link="logit"))

In [45]:
explainer.expected_value

array([0.5, 0.5, 0.5])

In [ ]:
shap.initjs()
for i in range(0,5):
    which_class= y_map_new['pred_label'][i]
    print(which_class)
    display(shap.force_plot(explainer.expected_value[which_class], shap.TreeExplainer(mcl).shap_values(X_test)[which_class][i],   X_test.values[i], feature_names = X_test.columns))

In [6]:
import matplotlib.pyplot as plt

model_dir= "../models/luad_lusc_healthy/"
output_dir= "../Output/luad_lusc_healthy/"

for i in range(1,6):
    
    # loading truly predicted test file
    newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str(i)+"_xgboost.csv")
    newdftest.index= newdftest["Sample"]
    newdftest=newdftest.drop(["Sample"], axis="columns")
    X_test= newdftest.copy() 
    print(X_test.shape)
    
    # loading truly predicted y_map
    y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost.csv")
    y_map_new.index= y_map_new["Sample"]
    y_map_new=y_map_new.drop(["Sample"], axis='columns')
    print(y_map_new.shape)
    
    # loading saved model
    mcl = xgb.XGBRFClassifier()
    mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost.json")
    
    # tree explainer; mcl is the model of xgboost
    explainer = shap.TreeExplainer(mcl)
    
    # calculating shap value
    out_list = []
    num_samples = np.shape(X_test)[0]
    for sample in tqdm(range(0,(num_samples))):
        # shap
        shap_values = explainer.shap_values(X_test[sample : sample + 1])
        out_list.append(shap_values)
        
    # squeezed; this the shap value for the test data
    shap_arr = np.squeeze(np.array(out_list))
    print(shap_arr.shape) # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of shap values
    
#     shap_df = filter_shap(X_test, shap_arr, pred, y_map_new)
    #shap_df = filter_shap(test_data, shap_arr, an_array)
    shap_df = filter_shap(X_test, shap_arr, y_map_new)
    
    # store shap value
    output_file = output_dir+f"treeExplainer_shap_scores_allGenes_test_"+str(i)+"_xgboost.pkl"
    pickle.dump(shap_df, open(str(output_file), "wb"))
    
    # class specific gene ranking 
    rank_df = get_rank_df(shap_df)
    rank_df.columns= ["healthy", "luad","lusc"]
    rank_df.to_csv(output_dir+"class_specific_gene_rank_test_"+str(i)+"_xgboost.csv")
    
#     shap.summary_plot(explainer.shap_values(X_test), X_test, plot_type="bar", class_names= rank_df.columns, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"global_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class healthy
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[0], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_healthy_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class luad
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[1], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_luad_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class lusc
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[2], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_lusc_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
    

(187, 19648)
(187, 4)


/aul/homes/msobh002/.conda/envs/concreteAE/lib/python3.9/site-packages/xgboost/core.py:158: UserWarning: [02:50:56] WARNING: /workspace/src/learner.cc:872: Found JSON model saved before XGBoost 1.6, please save the model using current version again. The support for old JSON model will be discontinued in XGBoost 2.3.
  warnings.warn(smsg, UserWarning)
  4%|▍         | 8/187 [00:35<13:20,  4.47s/it]


KeyboardInterrupt: 

(187, 3, 19648)


100%|██████████| 187/187 [00:00<00:00, 997.07it/s]

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


In [17]:
import matplotlib.pyplot as plt

model_dir= "../models/luad_lusc_healthy/"
output_dir= "../Output/luad_lusc_healthy/"

for i in range(1,6):
    
    # loading truly predicted test file
    newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str(i)+"_xgboost_nohp.csv")
    newdftest.index= newdftest["Sample"]
    newdftest=newdftest.drop(["Sample"], axis="columns")
    X_test= newdftest.copy() 
    print(X_test.shape)
    
    # loading truly predicted y_map
    y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost_nohp.csv")
    y_map_new.index= y_map_new["Sample"]
    y_map_new=y_map_new.drop(["Sample"], axis='columns')
    print(y_map_new.shape)
    
    # loading saved model
    mcl = xgb.XGBRFClassifier()
    mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost_nohp.json")
    
    # tree explainer; mcl is the model of xgboost
    explainer = shap.TreeExplainer(mcl)
    
    # calculating shap value
    out_list = []
    num_samples = np.shape(X_test)[0]
    for sample in tqdm(range(0,(num_samples))):
        # shap
        shap_values = explainer.shap_values(X_test[sample : sample + 1])
        out_list.append(shap_values)
        
    # squeezed; this the shap value for the test data
    shap_arr = np.squeeze(np.array(out_list))
    print(shap_arr.shape) # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of shap values
    
#     shap_df = filter_shap(X_test, shap_arr, pred, y_map_new)
    #shap_df = filter_shap(test_data, shap_arr, an_array)
    shap_df = filter_shap(X_test, shap_arr, y_map_new)
    
    # store shap value
    output_file = output_dir+f"treeExplainer_shap_scores_allGenes_test_"+str(i)+"_xgboost_nohp.pkl"
    pickle.dump(shap_df, open(str(output_file), "wb"))
    
    # class specific gene ranking 
    rank_df = get_rank_df(shap_df)
    rank_df.columns= ["healthy", "luad","lusc"]
    rank_df.to_csv(output_dir+"class_specific_gene_rank_test_"+str(i)+"_xgboost_nohp.csv")
    
#     shap.summary_plot(explainer.shap_values(X_test), X_test, plot_type="bar", class_names= rank_df.columns, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"global_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class healthy
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[0], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_healthy_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class luad
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[1], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_luad_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class lusc
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[2], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_lusc_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
    

(187, 19648)
(187, 4)


 47%|████▋     | 87/187 [00:22<00:26,  3.79it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 70%|███████   | 131/187 [00:34<00:14,  3.86it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 94%|█████████▎| 175/187 [00:45<00:03,  3.84it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 187/187 [00:49<00:00,  3.82it/s]


...

100%|██████████| 186/186 [00:48<00:00,  3.86it/s]


(186, 3, 19648)


100%|██████████| 186/186 [00:00<00:00, 956.61it/s]

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


In [70]:
# all random states

import matplotlib.pyplot as plt
import shap
import xgboost as xgb
import pandas as pd
import numpy as np
import pickle
from tqdm import tqdm

model_dir = "../models/luad_lusc_healthy/"
output_dir = "../Output/luad_lusc_healthy/"
random_states = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]

for random_state in random_states:
    print(f"Processing for Random State: {random_state}")
    
    for i in range(1, 6):
        # Loading truly predicted test file with specific random state
        newdftest = pd.read_csv(f"{output_dir}AfterDroppingFalsePrediction_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        newdftest.index = newdftest["Sample"]
        newdftest = newdftest.drop(["Sample"], axis="columns")
        X_test = newdftest.copy()
        print(X_test.shape)

        # Loading truly predicted y_map with specific random state
        y_map_new = pd.read_csv(f"{output_dir}true_predicted_label_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        y_map_new.index = y_map_new["Sample"]
        y_map_new = y_map_new.drop(["Sample"], axis='columns')
        print(y_map_new.shape)

        # Loading saved model with the specific random state
        mcl = xgb.XGBRFClassifier(random_state=random_state)
        mcl.load_model(f"{model_dir}fold_{i}_model_topology_xgboost_nohp_random_state_{random_state}.json")

        # Tree explainer; mcl is the model of xgboost
        explainer = shap.TreeExplainer(mcl)

        # Calculating SHAP values
        out_list = []
        num_samples = np.shape(X_test)[0]
        for sample in tqdm(range(num_samples)):
            # SHAP
            shap_values = explainer.shap_values(X_test[sample:sample + 1])
            out_list.append(shap_values)

        # Squeezed; this is the SHAP value for the test data
        shap_arr = np.squeeze(np.array(out_list))
        print(shap_arr.shape)  # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of SHAP values

        shap_df = filter_shap(X_test, shap_arr, y_map_new)

        # Store SHAP value
        output_file = output_dir + f"treeExplainer_shap_scores_allGenes_test_{i}_xgboost_nohp_random_state_{random_state}.pkl"
        pickle.dump(shap_df, open(str(output_file), "wb"))

        # Class-specific gene ranking
        rank_df = get_rank_df(shap_df)
        rank_df.columns = ["healthy", "luad", "lusc"]
        rank_df.to_csv(output_dir + f"class_specific_gene_rank_test_{i}_xgboost_nohp_random_state_{random_state}.csv")


Processing for Random State: 10
(187, 19648)
(187, 4)


 47%|████▋     | 87/187 [00:27<00:27,  3.67it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 70%|███████   | 131/187 [00:43<00:15,  3.61it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 94%|█████████▎| 175/187 [00:58<00:04,  2.45it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 187/187 [01:02<00:00,  2.99it/s]


...

100%|██████████| 186/186 [00:47<00:00,  3.93it/s]


(186, 3, 19648)


100%|██████████| 186/186 [00:00<00:00, 979.94it/s]

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0



DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


# LUAD LUSC

In [73]:
map_dict = {
    "healthy":0,
    "luad": 1,
    "lusc":2   
}

# filtering samlples based on true predicted label
# now each sample will have the shap value of only one class (truly predicted class)

def filter_shap(test_data, shap_arr, y_map_new):
    df_data = []
#     ids_list = X_test.index.to_list()
#     genes_list = X_test.columns.tolist()
    ids_list = test_data.index.to_list()
    genes_list = test_data.columns.tolist()
    genes_list= genes_list[0:19648]
#     print(shap_arr.shape)
    
    for i in tqdm(range(shap_arr.shape[0])):
        sample = shap_arr[i]
#         print(sample.shape)
        sample_id = ids_list[i]
#         print(sample_id)
        #print(y_pred[i])
        #label = inv_map[y_pred[i]]
        label = y_map_new['pred'][i]
#         print(label)
        label= map_dict[label]
#         print(label)
#         _, w, h = sample.shape
#         w, h = sample.shape
#         print(w,h)
        #print(sample[6])
#         shap_scores_flat = sample[label][: len(genes_list)]
        shap_scores_flat = sample
        #shap_scores_flat = np.reshape(sample[6], (w * h,))[: len(genes_list)]

        df_data.append([sample_id, *list(shap_scores_flat), label])

    shap_df = pd.DataFrame(
        data=np.array(df_data), columns=["id", *genes_list, "predicted_label"]
    )

    shap_df.set_index("id", inplace=True)
    shap_df["true_label"] = list(y_map_new['true_label'])
#     shap_df["predicted_label"] = shap_df["predicted_label"].astype("int").map(map_dict)
    #shap_df["predicted_label"] = shap_df["predicted_label"].map(map_dict)

    return shap_df



In [54]:
import matplotlib.pyplot as plt

model_dir= "../models/luad_lusc/"
output_dir= "../Output/luad_lusc/"

for i in range(1,6):
    
    # loading truly predicted test file
    newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str(i)+"_xgboost_nohp.csv")
    newdftest.index= newdftest["Sample"]
    newdftest=newdftest.drop(["Sample"], axis="columns")
    X_test= newdftest.copy() 
#     print(X_test.shape)
    
    # loading truly predicted y_map
    y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost_nohp.csv")
    y_map_new.index= y_map_new["Sample"]
    y_map_new=y_map_new.drop(["Sample"], axis='columns')
#     print(y_map_new.shape)
    
    # loading saved model
    mcl = xgb.XGBRFClassifier()
    mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost_nohp.json")
    
    # tree explainer; mcl is the model of xgboost
    explainer = shap.TreeExplainer(mcl)
    
    # calculating shap value
    out_list = []
    num_samples = np.shape(X_test)[0]
    for sample in tqdm(range(0,(num_samples))):
        # shap
        shap_values = explainer.shap_values(X_test[sample : sample + 1])
        out_list.append(shap_values)
        
    # squeezed; this the shap value for the test data
    shap_arr = np.squeeze(np.array(out_list))
#     print(shap_arr.shape) # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of shap values
    
#     shap_df = filter_shap(X_test, shap_arr, pred, y_map_new)
    #shap_df = filter_shap(test_data, shap_arr, an_array)
    shap_df = filter_shap(X_test, shap_arr, y_map_new)
    
    # store shap value
    output_file = output_dir+f"treeExplainer_shap_scores_allGenes_test_"+str(i)+"_xgboost_nohp.pkl"
    pickle.dump(shap_df, open(str(output_file), "wb"))
    
    # class specific gene ranking 
    rank_df = get_rank_df(shap_df)
    rank_df.columns= ["luad","lusc"]
    rank_df.to_csv(output_dir+"class_specific_gene_rank_test_"+str(i)+"_xgboost_nohp.csv")
    
#     shap.summary_plot(explainer.shap_values(X_test), X_test, plot_type="bar", class_names= rank_df.columns, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"global_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class healthy
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[0], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_healthy_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class luad
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[1], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_luad_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class lusc
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[2], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_lusc_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
    

(126, 19648)
(126, 4)


 69%|██████▉   | 87/126 [00:22<00:09,  3.93it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 126/126 [00:32<00:00,  3.93it/s]


(126, 19648)


100%|██████████| 126/126 [00:00<00:00, 1087.31it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


...

(124, 19648)
(124, 4)


 70%|███████   | 87/124 [00:22<00:09,  3.92it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 124/124 [00:31<00:00,  3.92it/s]


(124, 19648)


100%|██████████| 124/124 [00:00<00:00, 1105.14it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


In [74]:
# all random states

import matplotlib.pyplot as plt
import shap
import xgboost as xgb
import pandas as pd
import numpy as np
import pickle
from tqdm import tqdm

model_dir = "../models/luad_lusc/"
output_dir = "../Output/luad_lusc/"
random_states = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]

for random_state in random_states:
    print(f"Processing for Random State: {random_state}")
    
    for i in range(1, 6):
        # Loading truly predicted test file with specific random state
        newdftest = pd.read_csv(f"{output_dir}AfterDroppingFalsePrediction_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        newdftest.index = newdftest["Sample"]
        newdftest = newdftest.drop(["Sample"], axis="columns")
        X_test = newdftest.copy()
        print(X_test.shape)

        # Loading truly predicted y_map with specific random state
        y_map_new = pd.read_csv(f"{output_dir}true_predicted_label_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        y_map_new.index = y_map_new["Sample"]
        y_map_new = y_map_new.drop(["Sample"], axis='columns')
        print(y_map_new.shape)

        # Loading saved model with the specific random state
        mcl = xgb.XGBRFClassifier(random_state=random_state)
        mcl.load_model(f"{model_dir}fold_{i}_model_topology_xgboost_nohp_random_state_{random_state}.json")

        # Tree explainer; mcl is the model of xgboost
        explainer = shap.TreeExplainer(mcl)

        # Calculating SHAP values
        out_list = []
        num_samples = np.shape(X_test)[0]
        for sample in tqdm(range(num_samples)):
            # SHAP
            shap_values = explainer.shap_values(X_test[sample:sample + 1])
            out_list.append(shap_values)

        # Squeezed; this is the SHAP value for the test data
        shap_arr = np.squeeze(np.array(out_list))
        print(shap_arr.shape)  # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of SHAP values

        shap_df = filter_shap(X_test, shap_arr, y_map_new)

        # Store SHAP value
        output_file = output_dir + f"treeExplainer_shap_scores_allGenes_test_{i}_xgboost_nohp_random_state_{random_state}.pkl"
        pickle.dump(shap_df, open(str(output_file), "wb"))

        # Class-specific gene ranking
        rank_df = get_rank_df(shap_df)
        rank_df.columns = ["luad", "lusc"]
        rank_df.to_csv(output_dir + f"class_specific_gene_rank_test_{i}_xgboost_nohp_random_state_{random_state}.csv")

Processing for Random State: 10
(126, 19648)
(126, 4)


 69%|██████▉   | 87/126 [00:21<00:09,  3.94it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 126/126 [00:31<00:00,  3.97it/s]


(126, 19648)


100%|██████████| 126/126 [00:00<00:00, 1090.96it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


...

(124, 19648)
(124, 4)


 70%|███████   | 87/124 [00:22<00:09,  3.98it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 124/124 [00:31<00:00,  3.91it/s]


(124, 19648)


100%|██████████| 124/124 [00:00<00:00, 1062.77it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


# LUAD Healthy

In [75]:
map_dict = {
    "healthy":0,
    "luad": 1,
    "lusc":2   
}

# filtering samlples based on true predicted label
# now each sample will have the shap value of only one class (truly predicted class)

def filter_shap(test_data, shap_arr, y_map_new):
    df_data = []
#     ids_list = X_test.index.to_list()
#     genes_list = X_test.columns.tolist()
    ids_list = test_data.index.to_list()
    genes_list = test_data.columns.tolist()
    genes_list= genes_list[0:19648]
#     print(shap_arr.shape)
    
    for i in tqdm(range(shap_arr.shape[0])):
        sample = shap_arr[i]
#         print(sample.shape)
        sample_id = ids_list[i]
#         print(sample_id)
        #print(y_pred[i])
        #label = inv_map[y_pred[i]]
        label = y_map_new['pred'][i]
#         print(label)
        label= map_dict[label]
#         print(label)
#         _, w, h = sample.shape
#         w, h = sample.shape
#         print(w,h)
        #print(sample[6])
#         shap_scores_flat = sample[label][: len(genes_list)]
        shap_scores_flat = sample
        #shap_scores_flat = np.reshape(sample[6], (w * h,))[: len(genes_list)]

        df_data.append([sample_id, *list(shap_scores_flat), label])

    shap_df = pd.DataFrame(
        data=np.array(df_data), columns=["id", *genes_list, "predicted_label"]
    )

    shap_df.set_index("id", inplace=True)
    shap_df["true_label"] = list(y_map_new['true_label'])
#     shap_df["predicted_label"] = shap_df["predicted_label"].astype("int").map(map_dict)
    #shap_df["predicted_label"] = shap_df["predicted_label"].map(map_dict)

    return shap_df



In [57]:
import matplotlib.pyplot as plt

model_dir= "../models/luad_healthy/"
output_dir= "../Output/luad_healthy/"

for i in range(1,6):
    
    # loading truly predicted test file
    newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str(i)+"_xgboost_nohp.csv")
    newdftest.index= newdftest["Sample"]
    newdftest=newdftest.drop(["Sample"], axis="columns")
    X_test= newdftest.copy() 
    print(X_test.shape)
    
    # loading truly predicted y_map
    y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost_nohp.csv")
    y_map_new.index= y_map_new["Sample"]
    y_map_new=y_map_new.drop(["Sample"], axis='columns')
    print(y_map_new.shape)
    
    # loading saved model
    mcl = xgb.XGBRFClassifier()
    mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost_nohp.json")
    
    # tree explainer; mcl is the model of xgboost
    explainer = shap.TreeExplainer(mcl)
    
    # calculating shap value
    out_list = []
    num_samples = np.shape(X_test)[0]
    for sample in tqdm(range(0,(num_samples))):
        # shap
        shap_values = explainer.shap_values(X_test[sample : sample + 1])
        out_list.append(shap_values)
        
    # squeezed; this the shap value for the test data
    shap_arr = np.squeeze(np.array(out_list))
    print(shap_arr.shape) # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of shap values
    
#     shap_df = filter_shap(X_test, shap_arr, pred, y_map_new)
    #shap_df = filter_shap(test_data, shap_arr, an_array)
    shap_df = filter_shap(X_test, shap_arr, y_map_new)
    
    # store shap value
    output_file = output_dir+f"treeExplainer_shap_scores_allGenes_test_"+str(i)+"_xgboost_nohp.pkl"
    pickle.dump(shap_df, open(str(output_file), "wb"))
    
    # class specific gene ranking 
    rank_df = get_rank_df(shap_df)
    rank_df.columns= ["luad","lusc"]
    rank_df.to_csv(output_dir+"class_specific_gene_rank_test_"+str(i)+"_xgboost_nohp.csv")
    
#     shap.summary_plot(explainer.shap_values(X_test), X_test, plot_type="bar", class_names= rank_df.columns, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"global_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class healthy
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[0], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_healthy_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class luad
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[1], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_luad_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class lusc
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[2], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_lusc_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
    

(133, 19648)
(133, 4)


 65%|██████▌   | 87/133 [00:22<00:11,  3.92it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 98%|█████████▊| 131/133 [00:33<00:00,  3.93it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 133/133 [00:33<00:00,  3.92it/s]


(133, 19648)


...

 66%|██████▌   | 87/132 [00:22<00:11,  3.90it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 99%|█████████▉| 131/132 [00:33<00:00,  3.85it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 132/132 [00:33<00:00,  3.90it/s]


(132, 19648)


100%|██████████| 132/132 [00:00<00:00, 1089.01it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


In [76]:
# all random states

import matplotlib.pyplot as plt
import shap
import xgboost as xgb
import pandas as pd
import numpy as np
import pickle
from tqdm import tqdm

model_dir = "../models/luad_healthy/"
output_dir = "../Output/luad_healthy/"
random_states = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]

for random_state in random_states:
    print(f"Processing for Random State: {random_state}")
    
    for i in range(1, 6):
        # Loading truly predicted test file with specific random state
        newdftest = pd.read_csv(f"{output_dir}AfterDroppingFalsePrediction_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        newdftest.index = newdftest["Sample"]
        newdftest = newdftest.drop(["Sample"], axis="columns")
        X_test = newdftest.copy()
        print(X_test.shape)

        # Loading truly predicted y_map with specific random state
        y_map_new = pd.read_csv(f"{output_dir}true_predicted_label_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        y_map_new.index = y_map_new["Sample"]
        y_map_new = y_map_new.drop(["Sample"], axis='columns')
        print(y_map_new.shape)

        # Loading saved model with the specific random state
        mcl = xgb.XGBRFClassifier(random_state=random_state)
        mcl.load_model(f"{model_dir}fold_{i}_model_topology_xgboost_nohp_random_state_{random_state}.json")

        # Tree explainer; mcl is the model of xgboost
        explainer = shap.TreeExplainer(mcl)

        # Calculating SHAP values
        out_list = []
        num_samples = np.shape(X_test)[0]
        for sample in tqdm(range(num_samples)):
            # SHAP
            shap_values = explainer.shap_values(X_test[sample:sample + 1])
            out_list.append(shap_values)

        # Squeezed; this is the SHAP value for the test data
        shap_arr = np.squeeze(np.array(out_list))
        print(shap_arr.shape)  # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of SHAP values

        shap_df = filter_shap(X_test, shap_arr, y_map_new)

        # Store SHAP value
        output_file = output_dir + f"treeExplainer_shap_scores_allGenes_test_{i}_xgboost_nohp_random_state_{random_state}.pkl"
        pickle.dump(shap_df, open(str(output_file), "wb"))

        # Class-specific gene ranking
        rank_df = get_rank_df(shap_df)
        rank_df.columns = ["healthy", "luad"]
        rank_df.to_csv(output_dir + f"class_specific_gene_rank_test_{i}_xgboost_nohp_random_state_{random_state}.csv")


Processing for Random State: 10
(133, 19648)
(133, 4)


 65%|██████▌   | 87/133 [00:22<00:11,  3.89it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 98%|█████████▊| 131/133 [00:33<00:00,  3.61it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 133/133 [00:34<00:00,  3.85it/s]


(133, 19648)


...

 66%|██████▌   | 87/132 [00:21<00:11,  4.01it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


 99%|█████████▉| 131/132 [00:32<00:00,  4.00it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 132/132 [00:32<00:00,  4.00it/s]


(132, 19648)


100%|██████████| 132/132 [00:00<00:00, 1148.23it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


# LUSC Healthy

In [77]:
map_dict = {
    "healthy":0,
    "luad": 1,
    "lusc":2   
}

# filtering samlples based on true predicted label
# now each sample will have the shap value of only one class (truly predicted class)

def filter_shap(test_data, shap_arr, y_map_new):
    df_data = []
#     ids_list = X_test.index.to_list()
#     genes_list = X_test.columns.tolist()
    ids_list = test_data.index.to_list()
    genes_list = test_data.columns.tolist()
    genes_list= genes_list[0:19648]
#     print(shap_arr.shape)
    
    for i in tqdm(range(shap_arr.shape[0])):
        sample = shap_arr[i]
#         print(sample.shape)
        sample_id = ids_list[i]
#         print(sample_id)
        #print(y_pred[i])
        #label = inv_map[y_pred[i]]
        label = y_map_new['pred'][i]
#         print(label)
        label= map_dict[label]
#         print(label)
#         _, w, h = sample.shape
#         w, h = sample.shape
#         print(w,h)
        #print(sample[6])
#         shap_scores_flat = sample[label][: len(genes_list)]
        shap_scores_flat = sample
        #shap_scores_flat = np.reshape(sample[6], (w * h,))[: len(genes_list)]

        df_data.append([sample_id, *list(shap_scores_flat), label])

    shap_df = pd.DataFrame(
        data=np.array(df_data), columns=["id", *genes_list, "predicted_label"]
    )

    shap_df.set_index("id", inplace=True)
    shap_df["true_label"] = list(y_map_new['true_label'])
#     shap_df["predicted_label"] = shap_df["predicted_label"].astype("int").map(map_dict)
    #shap_df["predicted_label"] = shap_df["predicted_label"].map(map_dict)

    return shap_df



In [59]:
import matplotlib.pyplot as plt

model_dir= "../models/lusc_healthy/"
output_dir= "../Output/lusc_healthy/"

for i in range(1,6):
    
    # loading truly predicted test file
    newdftest= pd.read_csv(output_dir+"AfterDroppingFalsePrediction_test_"+str(i)+"_xgboost_nohp.csv")
    newdftest.index= newdftest["Sample"]
    newdftest=newdftest.drop(["Sample"], axis="columns")
    X_test= newdftest.copy() 
    print(X_test.shape)
    
    # loading truly predicted y_map
    y_map_new= pd.read_csv(output_dir+"true_predicted_label_test_"+str(i)+"_xgboost_nohp.csv")
    y_map_new.index= y_map_new["Sample"]
    y_map_new=y_map_new.drop(["Sample"], axis='columns')
    print(y_map_new.shape)
    
    # loading saved model
    mcl = xgb.XGBRFClassifier()
    mcl.load_model(model_dir+f"fold_"+ str(i)+"_model_topology_xgboost_nohp.json")
    
    # tree explainer; mcl is the model of xgboost
    explainer = shap.TreeExplainer(mcl)
    
    # calculating shap value
    out_list = []
    num_samples = np.shape(X_test)[0]
    for sample in tqdm(range(0,(num_samples))):
        # shap
        shap_values = explainer.shap_values(X_test[sample : sample + 1])
        out_list.append(shap_values)
        
    # squeezed; this the shap value for the test data
    shap_arr = np.squeeze(np.array(out_list))
    print(shap_arr.shape) # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of shap values
    
#     shap_df = filter_shap(X_test, shap_arr, pred, y_map_new)
    #shap_df = filter_shap(test_data, shap_arr, an_array)
    shap_df = filter_shap(X_test, shap_arr, y_map_new)
    
    # store shap value
    output_file = output_dir+f"treeExplainer_shap_scores_allGenes_test_"+str(i)+"_xgboost_nohp.pkl"
    pickle.dump(shap_df, open(str(output_file), "wb"))
    
    # class specific gene ranking 
    rank_df = get_rank_df(shap_df)
    rank_df.columns= ["luad","lusc"]
    rank_df.to_csv(output_dir+"class_specific_gene_rank_test_"+str(i)+"_xgboost_nohp.csv")
    
#     shap.summary_plot(explainer.shap_values(X_test), X_test, plot_type="bar", class_names= rank_df.columns, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"global_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class healthy
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[0], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_healthy_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class luad
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[1], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_luad_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
#     # summary plot specific class lusc
#     shap.summary_plot(shap.TreeExplainer(mcl).shap_values(X_test)[2], X_test.values, feature_names = X_test.columns, show=False)
#     plt.savefig(output_dir+"class_specific_lusc_interpretation_top_gene_rank_test_"+str(i)+"_xgboost.png")
#     plt.clf()
    
    

(121, 19648)
(121, 4)


 72%|███████▏  | 87/121 [00:22<00:08,  3.91it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 121/121 [00:30<00:00,  3.91it/s]


(121, 19648)


100%|██████████| 121/121 [00:00<00:00, 1110.71it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


...

(120, 19648)
(120, 4)


 72%|███████▎  | 87/120 [00:22<00:08,  3.89it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 120/120 [00:30<00:00,  3.91it/s]


(120, 19648)


100%|██████████| 120/120 [00:00<00:00, 1099.53it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


In [83]:
# all random states

import matplotlib.pyplot as plt
import shap
import xgboost as xgb
import pandas as pd
import numpy as np
import pickle
from tqdm import tqdm

model_dir = "../models/lusc_healthy/"
output_dir = "../Output/lusc_healthy/"
random_states = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]

for random_state in random_states:
    print(f"Processing for Random State: {random_state}")
    
    for i in range(1, 6):
        # Loading truly predicted test file with specific random state
        newdftest = pd.read_csv(f"{output_dir}AfterDroppingFalsePrediction_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        newdftest.index = newdftest["Sample"]
        newdftest = newdftest.drop(["Sample"], axis="columns")
        X_test = newdftest.copy()
        print(X_test.shape)

        # Loading truly predicted y_map with specific random state
        y_map_new = pd.read_csv(f"{output_dir}true_predicted_label_test_{i}_xgboost_nohp_random_state_{random_state}.csv")
        y_map_new.index = y_map_new["Sample"]
        y_map_new = y_map_new.drop(["Sample"], axis='columns')
        print(y_map_new.shape)

        # Loading saved model with the specific random state
        mcl = xgb.XGBRFClassifier(random_state=random_state)
        mcl.load_model(f"{model_dir}fold_{i}_model_topology_xgboost_nohp_random_state_{random_state}.json")

        # Tree explainer; mcl is the model of xgboost
        explainer = shap.TreeExplainer(mcl)

        # Calculating SHAP values
        out_list = []
        num_samples = np.shape(X_test)[0]
        for sample in tqdm(range(num_samples)):
            # SHAP
            shap_values = explainer.shap_values(X_test[sample:sample + 1])
            out_list.append(shap_values)

        # Squeezed; this is the SHAP value for the test data
        shap_arr = np.squeeze(np.array(out_list))
        print(shap_arr.shape)  # n sample, 3 output for 3 classes; 19648 features; each sample has 3 class of SHAP values

        shap_df = filter_shap(X_test, shap_arr, y_map_new)

        # Store SHAP value
        output_file = output_dir + f"treeExplainer_shap_scores_allGenes_test_{i}_xgboost_nohp_random_state_{random_state}.pkl"
        pickle.dump(shap_df, open(str(output_file), "wb"))

#         # Class-specific gene ranking
#         rank_df = get_rank_df(shap_df)
#         rank_df.columns = ["healthy", "lusc"]
#         rank_df.to_csv(output_dir + f"class_specific_gene_rank_test_{i}_xgboost_nohp_random_state_{random_state}.csv")


Processing for Random State: 10
(121, 19648)
(121, 4)


 72%|███████▏  | 87/121 [00:22<00:08,  3.93it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 121/121 [00:30<00:00,  3.93it/s]


(121, 19648)


100%|██████████| 121/121 [00:00<00:00, 1059.98it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`


...

(120, 19648)
(120, 4)


 72%|███████▎  | 87/120 [00:21<00:08,  3.98it/s]pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.


100%|██████████| 120/120 [00:30<00:00,  3.98it/s]


(120, 19648)


100%|██████████| 120/120 [00:00<00:00, 1065.67it/s]
DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
